In [1]:
%load_ext autoreload
%autoreload 2

import sys
sys.path.append('B://workspace/tensorflow/')

# 训练 Conv-LSTM 模型。
# 该模型通过同一个月的前 14 天的 SST 数据预测未来 1 天的 SST 数据。

# 导入数据集
from torch.utils.data import DataLoader

# 定义参数
OFFSET = 25000
WIDTH = 15
STEP = 1

In [20]:
from numpy import array
from torch.utils.data import random_split

from src.dataset.ERA5 import ERA5SSTDataset
from src.plot.sst import plot_sst_l, plot_sst_comparison

def get_lon(lon):
    lon_s = 360 + lon[0] if lon[0] <= 0 else lon[0]
    lon_e = 360 + lon[1] if lon[1] <= 0 else lon[1]
    
    print(lon_s, lon_e)
    
    return [lon_s, lon_e]

def split_data(area):
    lon = array(get_lon(area['lon']))
    lat = array(area['lat']) + 90

    dataset = ERA5SSTDataset(WIDTH, STEP, OFFSET, lon, lat)
    
    train_data_set, val_data_set, test_data_set = random_split(dataset, [0.7, 0.2, 0.1])

    train_dataloader = DataLoader(train_data_set, batch_size=15, shuffle=False)
    val_dataloader = DataLoader(val_data_set, batch_size=15, shuffle=False)
    test_dataloader = DataLoader(test_data_set, batch_size=15, shuffle=True)

    return train_dataloader, val_dataloader, test_dataloader

def get_sst(): 
    lon = array([-180, 180]) + 180
    lat = array([-90, 90]) + 90

    dataset = ERA5SSTDataset(WIDTH, STEP, OFFSET, lon, lat)
    loader = DataLoader(dataset, batch_size=1, shuffle=False)
    
    print(dataset.getTime(dataset.current))

    fore_, last_ = next(iter(loader))
    print(fore_.shape)

    return last_[0, :, :]

In [22]:
from src.trainer.transformer import train_transformer_model

model, test_ = train_transformer_model()


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name              | Type        | Params | Mode 
----------------------------------------------------------
0 | transformer       | Transformer | 7.4 M  | train
1 | input_projection  | Linear      | 205 K  | train
2 | output_projection | Linear      | 205 K  | train
----------------------------------------------------------
7.8 M     Trainable params
0         Non-trainable params
7.8 M     Total params
31.113    Total estimated model params size (MB)
57        Modules in train mode
0         Modules in eval mode


200 220
Epoch 199: 100%|██████████| 10/10 [00:05<00:00,  1.68it/s, v_num=12, train_loss=0.392]

`Trainer.fit` stopped: `max_epochs=200` reached.


Epoch 199: 100%|██████████| 10/10 [00:05<00:00,  1.68it/s, v_num=12, train_loss=0.392]
220 240


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name              | Type        | Params | Mode 
----------------------------------------------------------
0 | transformer       | Transformer | 7.4 M  | train
1 | input_projection  | Linear      | 205 K  | train
2 | output_projection | Linear      | 205 K  | train
----------------------------------------------------------
7.8 M     Trainable params
0         Non-trainable params
7.8 M     Total params
31.113    Total estimated model params size (MB)
57        Modules in train mode
0         Modules in eval mode


Epoch 199: 100%|██████████| 10/10 [00:05<00:00,  1.68it/s, v_num=13, train_loss=0.278]

`Trainer.fit` stopped: `max_epochs=200` reached.


Epoch 199: 100%|██████████| 10/10 [00:05<00:00,  1.68it/s, v_num=13, train_loss=0.278]


In [23]:
from sklearn.metrics import mean_squared_error

from src.config.params import Areas
from src.plot.base import create_shared_axes

axes = create_shared_axes(4, 3, 'all')

for area in Areas:
    train_dataloader, val_dataloader, test_dataloader = split_data(area)

    lon = array(get_lon(area['lon']))
    lat = array(area['lat']) + 90

    x_test, y_test = next(iter(test_dataloader))

    y_pred = model(x_test)

    g = y_pred[0, 0, :, :]
    y = y_test[0, 0, :, :]

    rmse = mean_squared_error(y.detach().numpy(), g.detach().numpy())
    print(f"RMSE: {rmse}")
    plot_sst_comparison(y.detach().numpy(), g.detach().numpy(), lon, lat)

200 220
200 220
RMSE: 38.27871322631836
220 240
220 240
RMSE: 0.3729950487613678
